In [1]:
import sys
sys.path.append("/Users/rohan/public_html/Hegemon")
import StepMiner as smn
import HegemonUtil as hu
import re
import numpy as np
import scipy
import io
from scipy import io
import math
import itertools
from itertools import combinations 
import matplotlib.pyplot as plt
%matplotlib inline
from matplotlib.backends.backend_pdf import PdfPages
import pandas as pd
import statsmodels.stats.proportion
import seaborn as sns
import scanpy as sc
import GEOparse
import os

In [9]:
%run ../moreprocessing.py

In [7]:
expr = pd.read_excel('GSE194234_mRNA_Diff_gene.FPKM.xlsx', header=0)
expr = expr.drop("gene_locus", axis = 1)
ih = pd.read_csv('GSE194234-GPL11154-ih.txt', sep = "\t", header = 0)
expr.columns = ["ProbeID", "Name"]+list(ih["ArrayID"])
expr

ProbeID      Name  GSM5831329  GSM5831330  GSM5831331  \
0    ENSG00000188290      HES4    9.116961    1.322078    3.695988   
1    ENSG00000187608     ISG15  396.620148   54.327911   92.358086   
2    ENSG00000188157      AGRN    5.310470    0.833227    1.139543   
3    ENSG00000180758    GPR157    1.827023    2.415529    1.820082   
4    ENSG00000116663     FBXO6   10.603917    7.952067    8.426725   
..               ...       ...         ...         ...         ...   
430  ENSG00000156052      GNAQ   48.809841   54.317736   55.262584   
431  ENSG00000274349    ZNF658    2.212057    1.544620    1.295261   
432  ENSG00000206077  ZDHHC11B    0.149390    0.380438    0.328249   
433  ENSG00000283378  CNTNAP3C   15.583185   20.964026   11.870526   
434  ENSG00000188672      RHCE    0.661573    2.134840    0.778879   

     GSM5831332  GSM5831333  GSM5831334  GSM5831335   GSM5831336  GSM5831337  \
0      4.480860    1.873886    2.215337   33.700775    25.260752   21.570292   
1    154.925858   21.222929   70.759140  832.458923  1588.175659  891.380493   
2      1.851625    0.237921    0.773402    7.503373    10.590167    8.777582   
3      2.351564    2.179383    1.994324    0.808418     0.808356    0.540218   
4      5.332705    3.418019    4.787608   15.126619    38.372734   14.370398   
..          ...         ...         ...         ...          ...         ...   
430   47.317362   48.619090   52.373090   21.701898    15.703751   20.723112   
431    2.907719    1.690877    3.056707    0.910815     0.229892    1.104339   
432    0.370596    0.258129    0.549899    0.172328     0.121480    0.060640   
433   15.649523    9.222829   18.616055    6.329426     1.849718    6.346222   
434    3.049084    4.659920    3.888372    0.343115     0.407393    0.694832   

     GSM5831338  GSM5831339  GSM5831340  GSM5831341  
0     35.479160    6.872925   31.388748   20.924770  
1    392.445099  660.305969  871.895813  695.775879  
2      7.421753    4.334783    7.863659    4.891538  
3      1.325827    1.140057    0.947273    0.936948  
4      6.809420   20.625580   14.600529   25.000597  
..          ...         ...         ...         ...  
430   38.195215   28.985347   26.248622   19.103288  
431    0.446855    0.454715    0.609426    0.246131  
432    0.173073    0.021263    0.213791    0.000000  
433    3.650172    4.986172    3.049874    0.817629  
434    1.167196    2.859171    1.870065    2.055218  

[435 rows x 15 columns]

In [10]:
# Log transform fpkm values

genes = pd.DataFrame()
genes["ProbeID"] = expr["ProbeID"]
genes["Name"] = expr["Name"]
cols = expr.columns

expr = expr.drop(['ProbeID', 'Name'], axis=1)
expr = sc.AnnData(expr.T)
sc.pp.log1p(expr, base = 2)

expr = pd.DataFrame(expr.X)
expr = expr.T
expr.insert(0, "Name", genes["Name"])
expr.insert(0, "ProbeID", genes["ProbeID"])
expr.columns = cols
expr

/usr/local/lib/python3.6/dist-packages/anndata/_core/anndata.py:119: ImplicitModificationWarning: Transforming to str index.
  warnings.warn("Transforming to str index.", ImplicitModificationWarning)


ProbeID      Name  GSM5831329  GSM5831330  GSM5831331  \
0    ENSG00000188290      HES4    3.338704    1.215416    2.231429   
1    ENSG00000187608     ISG15    8.635247    5.789936    6.544703   
2    ENSG00000188157      AGRN    2.657748    0.874385    1.097303   
3    ENSG00000180758    GPR157    1.499284    1.772109    1.495737   
4    ENSG00000116663     FBXO6    3.536540    3.162221    3.236757   
..               ...       ...         ...         ...         ...   
430  ENSG00000156052      GNAQ    5.638359    5.789670    5.814104   
431  ENSG00000274349    ZNF658    1.683498    1.347450    1.198658   
432  ENSG00000206077  ZDHHC11B    0.200868    0.465126    0.409526   
433  ENSG00000283378  CNTNAP3C    4.051649    4.457071    3.685999   
434  ENSG00000188672      RHCE    0.732550    1.648392    0.830968   

     GSM5831332  GSM5831333  GSM5831334  GSM5831335  GSM5831336  GSM5831337  \
0      2.454402    1.523003    1.684970    5.116896    4.714836    4.496353   
1      7.284717    4.473977    6.165091    9.702968   10.634063    9.801515   
2      1.511784    0.307919    0.826520    3.088035    3.534830    3.289478   
3      1.744835    1.668747    1.582230    0.854728    0.854679    0.623135   
4      2.662822    2.143400    2.532967    4.011372    5.299125    3.942082   
..          ...         ...         ...         ...         ...         ...   
430    5.594470    5.632823    5.738040    4.504741    4.062100    4.441159   
431    1.966327    1.428076    2.020309    0.934188    0.298532    1.073367   
432    0.454803    0.331280    0.632174    0.229376    0.165404    0.084935   
433    4.057409    3.353723    4.293963    2.873700    1.510819    2.877002   
434    2.017596    2.500782    2.289354    0.425583    0.493025    0.761142   

     GSM5831338  GSM5831339  GSM5831340  GSM5831341  
0      5.189001    2.976900    5.017421    4.454490  
1      8.620019    9.369174    9.769666    9.444551  
2      3.074120    2.415430    3.147902    2.558644  
3      1.217744    1.097649    0.961455    0.953785  
4      2.965215    4.434667    3.963523    4.700473  
..          ...         ...         ...         ...  
430    5.292605    4.906186    4.768111    4.329360  
431    0.532920    0.540737    0.686546    0.317456  
432    0.230293    0.030354    0.279520    0.000000  
433    2.217284    2.581634    2.017877    0.862058  
434    1.115830    1.948291    1.521083    1.611275  

[435 rows x 15 columns]

In [12]:
writeExprIdx(expr)

07-Jul-2022 13:06:23 DEBUG utils - Directory /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE194234 already exists. Skipping.
07-Jul-2022 13:06:23 INFO GEOparse - File already exist: using local version.
07-Jul-2022 13:06:23 INFO GEOparse - Parsing /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE194234/GSE194234_family.soft.gz: 
07-Jul-2022 13:06:23 DEBUG GEOparse - DATABASE: GeoMiame
07-Jul-2022 13:06:23 DEBUG GEOparse - SERIES: GSE194234
07-Jul-2022 13:06:23 DEBUG GEOparse - PLATFORM: GPL11154
07-Jul-2022 13:06:23 DEBUG GEOparse - SAMPLE: GSM5831329
07-Jul-2022 13:06:23 DEBUG GEOparse - SAMPLE: GSM5831330
07-Jul-2022 13:06:23 DEBUG GEOparse - SAMPLE: GSM5831331
07-Jul-2022 13:06:23 DEBUG GEOparse - SAMPLE: GSM5831332
07-Jul-2022 13:06:23 DEBUG GEOparse - SAMPLE: GSM5831333
07-Jul-2022 13:06:23 DEBUG GEOparse - SAMPLE: GSM5831334
07-Jul-2022 13:06:23 DEBUG GEOparse - SAMPLE: GSM5831335
07-Jul-2022 13:06:23 DEBUG GEOparse - SAMPLE: GSM5831336
07-Jul-2022 13:06:23 DEBU

Starting expr
Done writing expr
Starting make_idx
Done with make_idx


In [14]:
%run runmoreprocessing.py

Database ID NEU9
Dataset Name Peng 2022 Neutrophils
key macv:neu:
Configuration file (default /Users/rohan) 


07-Jul-2022 13:22:20 DEBUG utils - Directory /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE194234 already exists. Skipping.
07-Jul-2022 13:22:20 INFO GEOparse - File already exist: using local version.
07-Jul-2022 13:22:20 INFO GEOparse - Parsing /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE194234/GSE194234_family.soft.gz: 
07-Jul-2022 13:22:20 DEBUG GEOparse - DATABASE: GeoMiame
07-Jul-2022 13:22:20 DEBUG GEOparse - SERIES: GSE194234
07-Jul-2022 13:22:20 DEBUG GEOparse - PLATFORM: GPL11154
07-Jul-2022 13:22:20 DEBUG GEOparse - SAMPLE: GSM5831329
07-Jul-2022 13:22:20 DEBUG GEOparse - SAMPLE: GSM5831330
07-Jul-2022 13:22:20 DEBUG GEOparse - SAMPLE: GSM5831331
07-Jul-2022 13:22:20 DEBUG GEOparse - SAMPLE: GSM5831332
07-Jul-2022 13:22:20 DEBUG GEOparse - SAMPLE: GSM5831333
07-Jul-2022 13:22:20 DEBUG GEOparse - SAMPLE: GSM5831334
07-Jul-2022 13:22:20 DEBUG GEOparse - SAMPLE: GSM5831335
07-Jul-2022 13:22:20 DEBUG GEOparse - SAMPLE: GSM5831336
07-Jul-2022 13:22:20 DEBU

[NEU9]
name = Peng 2022 Neutrophils
expr = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE194234/GSE194234-GPL11154-expr.txt
index = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE194234/GSE194234-GPL11154-idx.txt
survival = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE194234/GSE194234-GPL11154-survival.txt
indexHeader = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE194234/GSE194234-GPL11154-ih.txt
info = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE194234/GSE194234-GPL11154-info.txt
key = macv:neu:
source = GSE194234
Write to file? y/n y


07-Jul-2022 13:22:22 DEBUG utils - Directory /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE194234 already exists. Skipping.
07-Jul-2022 13:22:22 INFO GEOparse - File already exist: using local version.
07-Jul-2022 13:22:22 INFO GEOparse - Parsing /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE194234/GSE194234_family.soft.gz: 
07-Jul-2022 13:22:22 DEBUG GEOparse - DATABASE: GeoMiame
07-Jul-2022 13:22:22 DEBUG GEOparse - SERIES: GSE194234
07-Jul-2022 13:22:22 DEBUG GEOparse - PLATFORM: GPL11154
07-Jul-2022 13:22:22 DEBUG GEOparse - SAMPLE: GSM5831329
07-Jul-2022 13:22:22 DEBUG GEOparse - SAMPLE: GSM5831330
07-Jul-2022 13:22:22 DEBUG GEOparse - SAMPLE: GSM5831331
07-Jul-2022 13:22:22 DEBUG GEOparse - SAMPLE: GSM5831332
07-Jul-2022 13:22:22 DEBUG GEOparse - SAMPLE: GSM5831333
07-Jul-2022 13:22:22 DEBUG GEOparse - SAMPLE: GSM5831334
07-Jul-2022 13:22:22 DEBUG GEOparse - SAMPLE: GSM5831335
07-Jul-2022 13:22:22 DEBUG GEOparse - SAMPLE: GSM5831336
07-Jul-2022 13:22:22 DEBU